In [9]:
import warnings
warnings.filterwarnings('ignore')

import pandas as pd
import numpy as np
import yfinance as yf
import hvplot.pandas
import seaborn as sns
from pathlib import Path
import requests
import json
#from MCForecastTools import MCSimulation

#%matplotlib inline


In [10]:
alpha_api = 'GQ3V6KMM3ISFS1NB'

# global variables 
indexes = 'SPY QQQ IWM DIA'
sectors = 'IYC IYH IYK IYR IYZ XLB XLE XLF XLI XLK XLU'
index_plus_sectors = indexes + ' ' + sectors

optionable_stocks_path = Path('./Resources/optionable_stocks.csv')
with open(optionable_stocks_path, 'r') as file:
    optionable_stocks = file.read()
optionable_stocks = optionable_stocks.replace('\n', ' ')

stocks_by_sector = pd.read_csv(Path('./Resources/stocks_by_sector.csv'), index_col='Ticker')

# dates
trading_days_year = 252
total_days_year = 365
thirty_years_ago = (pd.Timestamp.today() - pd.Timedelta(days = total_days_year * 30)).date()
ten_years_ago = (pd.Timestamp.today() - pd.Timedelta(days = total_days_year * 10)).date()
five_years_ago = (pd.Timestamp.today() - pd.Timedelta(days = total_days_year * 5)).date()
three_years_ago = (pd.Timestamp.today() - pd.Timedelta(days = total_days_year * 3)).date()
one_year = (pd.Timestamp.today() - pd.Timedelta(days = total_days_year * 1)).date()
six_months = (pd.Timestamp.today() - pd.Timedelta(days = total_days_year / 2)).date()
yesterday = (pd.Timestamp.today() - pd.Timedelta(days = 1)).date()


In [15]:
# method for getting close prices on a list of stocks
# important - don't put unnecessary spaces in the tickers, especially if it's a single ticker
def get_close(start, end, tickers = 'spy', interval = '1d'):
    
    if len(tickers) < 5:
        df = yf.Ticker(tickers)
        data = df.history(start=start, end=end, interval = interval)
        data = data['Close']
        data.dropna(inplace= True)
        data = data.rename(tickers)
    else:
        df = yf.Tickers(tickers)
        data = df.history(start=start, end=end, interval = interval)
        data = data['Close']
        data.dropna(inplace= True)    
        
    data.index = data.index.date
    return data

# method for getting cumulative return on a stock from a series of close prices
def get_cumprod(series):
    series = series.pct_change()
    series = (series + 1).cumprod()
    series.dropna(inplace= True)
    return series

# get correlation matrix from multiple series
def get_corr(stocks = []):
    all_stocks = pd.concat(stocks, axis=1).dropna()
    all_stocks = all_stocks.corr()
    return all_stocks

# method for getting er dates
def get_er_range(stock, api_key, delta = 10):
    url = f"https://www.alphavantage.co/query?function=EARNINGS&symbol={stock}&last=20&apikey={api_key}"
    response = requests.get(url)
    data = json.loads(response.text)
    df = pd.DataFrame(data['quarterlyEarnings'])
    df= pd.Series(df['reportedDate'])
    # convert the series to a datetime format
    dates = pd.to_datetime(df)
    # create an empty list to hold the new date ranges
    date_ranges = []
    # loop over each date in the series
    for date in dates:
        # create a date range for 10 days before and after the current date
        date_range = pd.date_range(date - pd.Timedelta(days=delta), date + pd.Timedelta(days=delta))
        # convert the date range to a Series object
        date_range_series = pd.Series(date_range)
        # add the date range to the list of date ranges
        date_ranges.append(date_range_series)
    # concatenate the list of date ranges into a single Series object
    new_dates = pd.concat(date_ranges)
    # remove any duplicates and sort the new series
    new_dates = pd.Series(sorted(set(new_dates)))
    # print the new series
    return new_dates


def get_income_statement(stock, api_key):
    url = f"https://www.alphavantage.co/query?function=INCOME_STATEMENT&symbol={stock}&last=20&apikey={api_key}"
    response = requests.get(url)
    data = json.loads(response.text)
    df = pd.DataFrame(data['quarterlyReports'])
    return df

def get_balance_sheet(stock, api_key):
    url = f"https://www.alphavantage.co/query?function=BALANCE_SHEET&symbol={stock}&last=20&apikey={api_key}"
    response = requests.get(url)
    data = json.loads(response.text)
    df = pd.DataFrame(data['quarterlyReports'])
    return df

# returns a df that has cumulative return for a set period for holding a stock vs holding it during er window
def comp_er_window(ticker, start, end, api_key):

    pct = get_close(start = start, end = end, tickers = ticker).pct_change()
    _range = get_er_range(ticker, api_key)

    standard_final = (pct + 1).cumprod().iloc[-1]
    pct = pct.reset_index()


    er_window = pd.concat([_range, pct], axis = 1, join = 'inner').drop('index', axis = 1)
    er_window.set_index(er_window.columns[0], inplace= True)
    er_window.dropna(inplace= True)
    er_final = (er_window + 1).cumprod().iloc[-1].values.astype(float)

    out = pd.DataFrame({
        "Buy and hold": standard_final,
        "Buy During Earnings": er_final
    })
    return out

# get a series of total returns on a weighted portfolio
def portfolio_returns(tickers, weights, start, end):
    portfolio = get_cumprod(get_close(start=start, end = end, tickers = tickers))
    return portfolio.dot(weights)

def get_pctchge(series_pct):
    series_pct = series_pct.pct_change()
    series_pct.dropna(inplace=True)
    return series_pct

def get_mean(series):
    series_m = series.mean()
    series_m = series_m*252
    
    return series_m
    
def get_std(series):
    series_sd = series.std()
    series_sd = series_sd*np.sqrt(252)
    
    return series_sd

def get_sharpe(series_m, series_sd):
    series_sharpe = (series_m - 0.05) / series_sd
    
    return series_sharpe

# Market Statistics Report

## Returns and Risk Analysis: Index, Sector and Stocks

In [12]:

#risk_free_rate = get_close(thirty_years_ago, yesterday, '^irx')
#combined = pd.concat([sectors, risk_free_rate], join = 'inner', axis = 1)
#combined

In [13]:

sectors_30_daily = get_close(thirty_years_ago, yesterday, tickers = index_plus_sectors)
sectors_10_daily = get_close(ten_years_ago, yesterday, tickers = index_plus_sectors)
sectors_5_daily = get_close(five_years_ago, yesterday, tickers = index_plus_sectors)
sectors_3_daily = get_close(three_years_ago, yesterday, tickers = index_plus_sectors)
sectors_1_daily = get_close(one_year, yesterday, tickers = index_plus_sectors)

[*********************100%***********************]  15 of 15 completed
[*********************100%***********************]  15 of 15 completed
[*********************100%***********************]  15 of 15 completed
[*********************100%***********************]  15 of 15 completed
[*********************100%***********************]  15 of 15 completed


In [16]:
ind_sec_1y = get_pctchge(sectors_1_daily)
ind_sec_1y_m = get_mean(ind_sec_1y)
ind_sec_1y_sd = get_std(ind_sec_1y)
ind_sec_1y_sr = get_sharpe(ind_sec_1y_m, ind_sec_1y_sd)

ind_sec_1y_m = ind_sec_1y_m.sort_values(ascending=False)
ind_sec_1y_sd = ind_sec_1y_sd.sort_values(ascending=False)
ind_sec_1y_sr = ind_sec_1y_sr.sort_values(ascending=False)

print(ind_sec_1y_m)
print(ind_sec_1y_sd)
print(ind_sec_1y_sr)

XLK    0.166640
XLE    0.152998
QQQ    0.131787
XLI    0.106942
IYH    0.097716
DIA    0.080434
SPY    0.077059
IYC    0.076473
IWM    0.046835
IYK    0.040770
XLB    0.025065
XLU    0.015979
XLF    0.000558
IYR   -0.058489
IYZ   -0.128469
dtype: float64
XLE    0.334247
XLK    0.292104
QQQ    0.283407
IYC    0.279640
IWM    0.258085
IYR    0.244676
XLB    0.241636
IYZ    0.237833
XLF    0.232173
SPY    0.219364
XLU    0.216544
XLI    0.212584
DIA    0.182171
IYH    0.172509
IYK    0.155530
dtype: float64
XLK    0.399309
XLE    0.308149
QQQ    0.288583
IYH    0.276599
XLI    0.267855
DIA    0.167065
SPY    0.123353
IYC    0.094667
IWM   -0.012264
IYK   -0.059345
XLB   -0.103192
XLU   -0.157107
XLF   -0.212955
IYR   -0.443396
IYZ   -0.750396
dtype: float64


In [7]:
ind_sec_3y = get_pctchge(sectors_3_daily)
ind_sec_3y_m = get_mean(ind_sec_3y)
ind_sec_3y_sd = get_std(ind_sec_3y)
ind_sec_3y_sr = get_sharpe(ind_sec_3y_m, ind_sec_3y_sd)

ind_sec_3y_m = ind_sec_1y_m.sort_values(ascending=False)
ind_sec_3y_sd = ind_sec_1y_sd.sort_values(ascending=False)
ind_sec_3y_sr = ind_sec_1y_sr.sort_values(ascending=False)

print(ind_sec_3y_m)
print(ind_sec_3y_sd)
print(ind_sec_3y_sr)

XLK    0.166640
XLE    0.152998
QQQ    0.131787
XLI    0.106942
IYH    0.097716
DIA    0.080435
SPY    0.077059
IYC    0.076473
IWM    0.046835
IYK    0.040770
XLB    0.025065
XLU    0.015979
XLF    0.000558
IYR   -0.058489
IYZ   -0.128469
dtype: float64
XLE    0.334247
XLK    0.292104
QQQ    0.283407
IYC    0.279640
IWM    0.258085
IYR    0.244676
XLB    0.241636
IYZ    0.237833
XLF    0.232173
SPY    0.219364
XLU    0.216544
XLI    0.212584
DIA    0.182171
IYH    0.172509
IYK    0.155530
dtype: float64
XLK    0.399309
XLE    0.308149
QQQ    0.288583
IYH    0.276598
XLI    0.267855
DIA    0.167066
SPY    0.123353
IYC    0.094668
IWM   -0.012264
IYK   -0.059345
XLB   -0.103192
XLU   -0.157107
XLF   -0.212955
IYR   -0.443396
IYZ   -0.750396
dtype: float64


In [8]:
ind_sec_5y = get_pctchge(sectors_5_daily)
ind_sec_5y_m = get_mean(ind_sec_5y)
ind_sec_5y_sd = get_std(ind_sec_5y)
ind_sec_5y_sr = get_sharpe(ind_sec_5y_m, ind_sec_5y_sd)

ind_sec_5y_m = ind_sec_1y_m.sort_values(ascending=False)
ind_sec_5y_sd = ind_sec_1y_sd.sort_values(ascending=False)
ind_sec_5y_sr = ind_sec_1y_sr.sort_values(ascending=False)

print(ind_sec_5y_m)
print(ind_sec_5y_sd)
print(ind_sec_5y_sr)

XLK    0.166640
XLE    0.152998
QQQ    0.131787
XLI    0.106942
IYH    0.097716
DIA    0.080435
SPY    0.077059
IYC    0.076473
IWM    0.046835
IYK    0.040770
XLB    0.025065
XLU    0.015979
XLF    0.000558
IYR   -0.058489
IYZ   -0.128469
dtype: float64
XLE    0.334247
XLK    0.292104
QQQ    0.283407
IYC    0.279640
IWM    0.258085
IYR    0.244676
XLB    0.241636
IYZ    0.237833
XLF    0.232173
SPY    0.219364
XLU    0.216544
XLI    0.212584
DIA    0.182171
IYH    0.172509
IYK    0.155530
dtype: float64
XLK    0.399309
XLE    0.308149
QQQ    0.288583
IYH    0.276598
XLI    0.267855
DIA    0.167066
SPY    0.123353
IYC    0.094668
IWM   -0.012264
IYK   -0.059345
XLB   -0.103192
XLU   -0.157107
XLF   -0.212955
IYR   -0.443396
IYZ   -0.750396
dtype: float64


In [9]:
ind_sec_10y = get_pctchge(sectors_10_daily)
ind_sec_10y_m = get_mean(ind_sec_10y)
ind_sec_10y_sd = get_std(ind_sec_10y)
ind_sec_10y_sr = get_sharpe(ind_sec_10y_m, ind_sec_10y_sd)

ind_sec_10y_m = ind_sec_10y_m.sort_values(ascending=False)
ind_sec_10y_sd = ind_sec_10y_sd.sort_values(ascending=False)
ind_sec_10y_sr = ind_sec_10y_sr.sort_values(ascending=False)

print(ind_sec_10y_m)
print(ind_sec_10y_sd)
print(ind_sec_10y_sr)

XLK    0.196492
QQQ    0.180933
IYH    0.130900
SPY    0.126820
XLI    0.122093
IYK    0.118005
IYC    0.117359
DIA    0.117071
XLF    0.116676
XLB    0.109410
XLU    0.106632
IWM    0.096474
XLE    0.082171
IYR    0.068095
IYZ    0.020913
dtype: float64
XLE    0.296124
XLK    0.223293
XLF    0.221669
IWM    0.218534
QQQ    0.213263
XLB    0.205487
IYR    0.198763
XLI    0.196260
IYC    0.190888
IYZ    0.190088
XLU    0.188994
SPY    0.175116
DIA    0.174373
IYH    0.172836
IYK    0.155632
dtype: float64
XLK    0.656052
QQQ    0.613951
IYH    0.468072
SPY    0.438684
IYK    0.436960
DIA    0.384643
XLI    0.367335
IYC    0.352871
XLF    0.300791
XLU    0.299651
XLB    0.289117
IWM    0.212664
XLE    0.108640
IYR    0.091039
IYZ   -0.153019
dtype: float64


In [10]:
ind_sec_30y = get_pctchge(sectors_30_daily)
ind_sec_30y_m = get_mean(ind_sec_30y)
ind_sec_30y_sd = get_std(ind_sec_30y)
ind_sec_30y_sr = get_sharpe(ind_sec_30y_m, ind_sec_30y_sd)

ind_sec_30y_m = ind_sec_1y_m.sort_values(ascending=False)
ind_sec_30y_sd = ind_sec_1y_sd.sort_values(ascending=False)
ind_sec_30y_sr = ind_sec_1y_sr.sort_values(ascending=False)

print(ind_sec_30y_m)
print(ind_sec_30y_sd)
print(ind_sec_30y_sr)

XLK    0.166640
XLE    0.152998
QQQ    0.131787
XLI    0.106942
IYH    0.097716
DIA    0.080435
SPY    0.077059
IYC    0.076473
IWM    0.046835
IYK    0.040770
XLB    0.025065
XLU    0.015979
XLF    0.000558
IYR   -0.058489
IYZ   -0.128469
dtype: float64
XLE    0.334247
XLK    0.292104
QQQ    0.283407
IYC    0.279640
IWM    0.258085
IYR    0.244676
XLB    0.241636
IYZ    0.237833
XLF    0.232173
SPY    0.219364
XLU    0.216544
XLI    0.212584
DIA    0.182171
IYH    0.172509
IYK    0.155530
dtype: float64
XLK    0.399309
XLE    0.308149
QQQ    0.288583
IYH    0.276598
XLI    0.267855
DIA    0.167066
SPY    0.123353
IYC    0.094668
IWM   -0.012264
IYK   -0.059345
XLB   -0.103192
XLU   -0.157107
XLF   -0.212955
IYR   -0.443396
IYZ   -0.750396
dtype: float64


In [11]:
ind_sec_1y_df = pd.concat([ind_sec_1y_m,  ind_sec_1y_sd, ind_sec_1y_sr], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio"]
ind_sec_1y_df.columns = columns
ind_sec_1y_df

Mean   Std Dev  Sharpe Ratio
XLK  0.166640  0.292104      0.399309
XLE  0.152998  0.334247      0.308149
QQQ  0.131787  0.283407      0.288583
XLI  0.106942  0.212584      0.267855
IYH  0.097716  0.172509      0.276598
DIA  0.080435  0.182171      0.167066
SPY  0.077059  0.219364      0.123353
IYC  0.076473  0.279640      0.094668
IWM  0.046835  0.258085     -0.012264
IYK  0.040770  0.155530     -0.059345
XLB  0.025065  0.241636     -0.103192
XLU  0.015979  0.216544     -0.157107
XLF  0.000558  0.232173     -0.212955
IYR -0.058489  0.244676     -0.443396
IYZ -0.128469  0.237833     -0.750396

In [12]:
ind_sec_3y_df = pd.concat([ind_sec_3y_m,  ind_sec_3y_sd, ind_sec_3y_sr], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio"]
ind_sec_3y_df.columns = columns
ind_sec_3y_df

Mean   Std Dev  Sharpe Ratio
XLK  0.166640  0.292104      0.399309
XLE  0.152998  0.334247      0.308149
QQQ  0.131787  0.283407      0.288583
XLI  0.106942  0.212584      0.267855
IYH  0.097716  0.172509      0.276598
DIA  0.080435  0.182171      0.167066
SPY  0.077059  0.219364      0.123353
IYC  0.076473  0.279640      0.094668
IWM  0.046835  0.258085     -0.012264
IYK  0.040770  0.155530     -0.059345
XLB  0.025065  0.241636     -0.103192
XLU  0.015979  0.216544     -0.157107
XLF  0.000558  0.232173     -0.212955
IYR -0.058489  0.244676     -0.443396
IYZ -0.128469  0.237833     -0.750396

In [13]:
ind_sec_5y_df = pd.concat([ind_sec_5y_m,  ind_sec_5y_sd, ind_sec_5y_sr], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio"]
ind_sec_5y_df.columns = columns
ind_sec_5y_df

Mean   Std Dev  Sharpe Ratio
XLK  0.166640  0.292104      0.399309
XLE  0.152998  0.334247      0.308149
QQQ  0.131787  0.283407      0.288583
XLI  0.106942  0.212584      0.267855
IYH  0.097716  0.172509      0.276598
DIA  0.080435  0.182171      0.167066
SPY  0.077059  0.219364      0.123353
IYC  0.076473  0.279640      0.094668
IWM  0.046835  0.258085     -0.012264
IYK  0.040770  0.155530     -0.059345
XLB  0.025065  0.241636     -0.103192
XLU  0.015979  0.216544     -0.157107
XLF  0.000558  0.232173     -0.212955
IYR -0.058489  0.244676     -0.443396
IYZ -0.128469  0.237833     -0.750396

In [14]:
ind_sec_10y_df = pd.concat([ind_sec_10y_m,  ind_sec_10y_sd, ind_sec_10y_sr], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio"]
ind_sec_10y_df.columns = columns
ind_sec_10y_df

Mean   Std Dev  Sharpe Ratio
XLK  0.196492  0.223293      0.656052
QQQ  0.180933  0.213263      0.613951
IYH  0.130900  0.172836      0.468072
SPY  0.126820  0.175116      0.438684
XLI  0.122093  0.196260      0.367335
IYK  0.118005  0.155632      0.436960
IYC  0.117359  0.190888      0.352871
DIA  0.117071  0.174373      0.384643
XLF  0.116676  0.221669      0.300791
XLB  0.109410  0.205487      0.289117
XLU  0.106632  0.188994      0.299651
IWM  0.096474  0.218534      0.212664
XLE  0.082171  0.296124      0.108640
IYR  0.068095  0.198763      0.091039
IYZ  0.020913  0.190088     -0.153019

In [15]:
ind_sec_30y_df = pd.concat([ind_sec_30y_m,  ind_sec_30y_sd, ind_sec_30y_sr], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio"]
ind_sec_30y_df.columns = columns
ind_sec_30y_df

Mean   Std Dev  Sharpe Ratio
XLK  0.166640  0.292104      0.399309
XLE  0.152998  0.334247      0.308149
QQQ  0.131787  0.283407      0.288583
XLI  0.106942  0.212584      0.267855
IYH  0.097716  0.172509      0.276598
DIA  0.080435  0.182171      0.167066
SPY  0.077059  0.219364      0.123353
IYC  0.076473  0.279640      0.094668
IWM  0.046835  0.258085     -0.012264
IYK  0.040770  0.155530     -0.059345
XLB  0.025065  0.241636     -0.103192
XLU  0.015979  0.216544     -0.157107
XLF  0.000558  0.232173     -0.212955
IYR -0.058489  0.244676     -0.443396
IYZ -0.128469  0.237833     -0.750396

In [16]:
ind_sec_1y_df.hvplot.scatter(x='Std Dev', y='Mean', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 1-Year View of Index & Sector Returns')

:Scatter   [Std Dev]   (Mean)

In [17]:
ind_sec_3y_df.hvplot.scatter(x='Std Dev', y='Mean', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 3-Year View of Index & Sector Returns')

:Scatter   [Std Dev]   (Mean)

In [18]:
ind_sec_5y_df.hvplot.scatter(x='Std Dev', y='Mean', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 5-Year View of Index & Sector Returns')

:Scatter   [Std Dev]   (Mean)

In [19]:
ind_sec_10y_df.hvplot.scatter(x='Std Dev', y='Mean', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 10-Year View of Index & Sector Returns')

:Scatter   [Std Dev]   (Mean)

In [20]:
ind_sec_30y_df.hvplot.scatter(x='Std Dev', y='Mean', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 30-Year View of Index & Sector Returns')

:Scatter   [Std Dev]   (Mean)

In [21]:

sectors = get_cumprod(get_close(thirty_years_ago, yesterday, tickers = index_plus_sectors))
sectors_10 = get_cumprod(get_close(ten_years_ago, yesterday, tickers = index_plus_sectors))
sectors_5 = get_cumprod(get_close(five_years_ago, yesterday, tickers = index_plus_sectors))
sectors_3 = get_cumprod(get_close(three_years_ago, yesterday, tickers = index_plus_sectors))
sectors_1 = get_cumprod(get_close(one_year, yesterday, tickers = index_plus_sectors))

[*********************100%***********************]  15 of 15 completed
[*********************100%***********************]  15 of 15 completed
[*********************100%***********************]  15 of 15 completed
[*********************100%***********************]  15 of 15 completed
[*********************100%***********************]  15 of 15 completed


In [22]:
sectors_1.hvplot().opts(height = 400,
                     width = 1000, title = 'Cumulative Returns for Index & Sectors - 1-year View')

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [17]:

sectors_1_cum = sectors_1.iloc[-1:]
sectors_1_cum = sectors_1_cum.transpose()
columns = ["Close"]
sectors_1_cum.columns = columns
sectors_1_cum["CumRet"] = (sectors_1_cum['Close'] - 1)*100
sectors_1_cum = sectors_1_cum.sort_values('CumRet', ascending=False)
sectors_1_cum = sectors_1_cum.drop('Close', axis=1)
sectors_1_cum.index = sectors_1_cum.index.rename('Index')
sectors_1_cum.index.rename('Index', inplace=True)

sectors_1_cum = sectors_1_cum.rename(index={'DIA': 'Dow Ind',
                                            'IWM': 'Russell',
                                            'IYC': 'Cons Disc',
                                            'IYH': 'Healthcare',
                                            'IYK': 'Cons Stple',
                                            'IYR': 'Real Est.',
                                            'IYZ': 'Comm',
                                            'QQQ': 'NASDAQ',
                                            'SPY': 'S&P 500',
                                            'XLB': 'Materials',
                                            'XLE': 'Energy',
                                            'XLF': 'Financials',
                                            'XLI': 'Industrials',
                                            'XLK': 'Technology',
                                            'XLU': 'Utilities'})


sectors_1_bchart = sectors_1_cum.hvplot.bar(xlabel='Index', ylabel='CumRet', hover_color='red', ylim=(-20, 20), height=500, width=1000).opts(
    yformatter='%.0f', title='Index and Sector Cumulative Returns Ranking - 1 Year Window')

sectors_1_bchart

NameError: name 'sectors_1' is not defined

In [24]:
sectors_3.hvplot().opts(height = 400,
                     width = 1000, title = 'Cumulative Returns for Index & Sectors - 3-year View')

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [25]:
sectors_3_cum = sectors_3.iloc[-1:]
sectors_3_cum = sectors_3_cum.transpose()
columns = ["Close"]
sectors_3_cum.columns = columns
sectors_3_cum["CumRet"] = (sectors_3_cum['Close'] - 1)*100
sectors_3_cum = sectors_3_cum.sort_values('CumRet', ascending=False)
sectors_3_cum = sectors_3_cum.drop('Close', axis=1)
sectors_3_cum.index = sectors_3_cum.index.rename('Index')
sectors_3_cum.index.rename('Index', inplace=True)

sectors_3_cum = sectors_3_cum.rename(index={'DIA': 'Dow Ind',
                                            'IWM': 'Russell',
                                            'IYC': 'Cons Disc',
                                            'IYH': 'Healthcare',
                                            'IYK': 'Cons Stple',
                                            'IYR': 'Real Est.',
                                            'IYZ': 'Comm',
                                            'QQQ': 'NASDAQ',
                                            'SPY': 'S&P 500',
                                            'XLB': 'Materials',
                                            'XLE': 'Energy',
                                            'XLF': 'Financials',
                                            'XLI': 'Industrials',
                                            'XLK': 'Technology',
                                            'XLU': 'Utilities'})


sectors_3_bchart = sectors_3_cum.hvplot.bar(xlabel='Index', ylabel='CumRet', hover_color='red', ylim=(-50, 200), height=500, width=1000).opts(
    yformatter='%.0f', title='Index and Sector Cumulative Returns Ranking - 3 Year Window')

sectors_3_bchart

:Bars   [Index]   (CumRet)

In [26]:
sectors_5.hvplot().opts(height = 400,
                     width = 1000, title = 'Cumulative Returns for Index & Sectors - 5-year View')

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [27]:
sectors_5_cum = sectors_5.iloc[-1:]
sectors_5_cum = sectors_5_cum.transpose()
columns = ["Close"]
sectors_5_cum.columns = columns
sectors_5_cum["CumRet"] = (sectors_5_cum['Close'] - 1)*100
sectors_5_cum = sectors_5_cum.sort_values('CumRet', ascending=False)
sectors_5_cum = sectors_5_cum.drop('Close', axis=1)
sectors_5_cum.index = sectors_5_cum.index.rename('Index')
sectors_5_cum.index.rename('Index', inplace=True)

sectors_5_cum = sectors_5_cum.rename(index={'DIA': 'Dow Ind',
                                            'IWM': 'Russell',
                                            'IYC': 'Cons Disc',
                                            'IYH': 'Healthcare',
                                            'IYK': 'Cons Stple',
                                            'IYR': 'Real Est.',
                                            'IYZ': 'Comm',
                                            'QQQ': 'NASDAQ',
                                            'SPY': 'S&P 500',
                                            'XLB': 'Materials',
                                            'XLE': 'Energy',
                                            'XLF': 'Financials',
                                            'XLI': 'Industrials',
                                            'XLK': 'Technology',
                                            'XLU': 'Utilities'})


sectors_5_bchart = sectors_5_cum.hvplot.bar(xlabel='Index', ylabel='CumRet', hover_color='red', ylim=(-50, 200), height=500, width=1000).opts(
    yformatter='%.0f', title='Index and Sector Cumulative Returns Ranking - 5 Year Window')

sectors_5_bchart

:Bars   [Index]   (CumRet)

In [28]:
sectors_10.hvplot().opts(height = 400,
                     width = 1000, title = 'Cumulative Returns for Index & Sectors - 10-year View')

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [29]:
sectors_10_cum = sectors_10.iloc[-1:]
sectors_10_cum = sectors_10_cum.transpose()
columns = ["Close"]
sectors_10_cum.columns = columns
sectors_10_cum["CumRet"] = (sectors_10_cum['Close'] - 1)*100
sectors_10_cum = sectors_10_cum.sort_values('CumRet', ascending=False)
sectors_10_cum = sectors_10_cum.drop('Close', axis=1)
sectors_10_cum.index = sectors_10_cum.index.rename('Index')
sectors_10_cum.index.rename('Index', inplace=True)

sectors_10_cum = sectors_10_cum.rename(index={'DIA': 'Dow Ind',
                                            'IWM': 'Russell',
                                            'IYC': 'Cons Disc',
                                            'IYH': 'Healthcare',
                                            'IYK': 'Cons Stple',
                                            'IYR': 'Real Est.',
                                            'IYZ': 'Comm',
                                            'QQQ': 'NASDAQ',
                                            'SPY': 'S&P 500',
                                            'XLB': 'Materials',
                                            'XLE': 'Energy',
                                            'XLF': 'Financials',
                                            'XLI': 'Industrials',
                                            'XLK': 'Technology',
                                            'XLU': 'Utilities'})


sectors_10_bchart = sectors_10_cum.hvplot.bar(xlabel='Index', ylabel='CumRet', hover_color='red', ylim=(-10, 500), height=500, width=1000).opts(
    yformatter='%.0f', title='Index and Sector Cumulative Returns Ranking - 10 Year Window')

sectors_10_bchart

:Bars   [Index]   (CumRet)

In [30]:
sectors.hvplot().opts(height = 400,
                     width = 1000, title = 'Cumulative Returns for Index & Sectors - 30-year View')

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [31]:
sectors_30_cum = sectors.iloc[-1:]
sectors_30_cum = sectors_30_cum.transpose()
columns = ["Close"]
sectors_30_cum.columns = columns
sectors_30_cum["CumRet"] = (sectors_30_cum['Close'] - 1)*100
sectors_30_cum = sectors_30_cum.sort_values('CumRet', ascending=False)
sectors_30_cum = sectors_30_cum.drop('Close', axis=1)
sectors_30_cum.index = sectors_30_cum.index.rename('Index')
sectors_30_cum.index.rename('Index', inplace=True)

sectors_30_cum = sectors_30_cum.rename(index={'DIA': 'Dow Ind',
                                            'IWM': 'Russell',
                                            'IYC': 'Cons Disc',
                                            'IYH': 'Healthcare',
                                            'IYK': 'Cons Stple',
                                            'IYR': 'Real Est.',
                                            'IYZ': 'Comm',
                                            'QQQ': 'NASDAQ',
                                            'SPY': 'S&P 500',
                                            'XLB': 'Materials',
                                            'XLE': 'Energy',
                                            'XLF': 'Financials',
                                            'XLI': 'Industrials',
                                            'XLK': 'Technology',
                                            'XLU': 'Utilities'})


sectors_30_bchart = sectors_30_cum.hvplot.bar(xlabel='Index', ylabel='CumRet', hover_color='red', ylim=(-50, 800), height=500, width=1000).opts(
    yformatter='%.0f', title='Index and Sector Cumulative Returns Ranking - 30 Year Window')

sectors_30_bchart

:Bars   [Index]   (CumRet)

In [32]:

stock_prices = get_close(one_year, yesterday, optionable_stocks)

stk_ret_1y = get_pctchge(stock_prices)
stk_ret_1y_m = get_mean(stk_ret_1y)
stk_ret_1y_sd = get_std(stk_ret_1y)
stk_ret_1y_sr = get_sharpe(stk_ret_1y_m, stk_ret_1y_sd)

stk_ret_1y_m = stk_ret_1y_m.sort_values(ascending=False)
stk_ret_1y_sd = stk_ret_1y_sd.sort_values(ascending=False)
stk_ret_1y_sr = stk_ret_1y_sr.sort_values(ascending=False)

print(stk_ret_1y_m)
print(stk_ret_1y_sd)
print(stk_ret_1y_sr)

[*********************100%***********************]  95 of 95 completed
NFLX    0.762248
MARA    0.722565
NVDA    0.698078
GE      0.623715
SPOT    0.558349
          ...   
MMM    -0.308498
LUV    -0.323632
BYND   -0.481058
SNAP   -0.508210
DISH   -0.900520
Length: 95, dtype: float64
MARA    1.344453
SNAP    0.972409
BYND    0.920945
PLUG    0.807898
ROKU    0.801836
          ...   
PG      0.201397
BMY     0.200578
KO      0.180205
PEP     0.178383
JNJ     0.167692
Length: 95, dtype: float64
GE      1.871859
CAH     1.602214
MRK     1.452194
NFLX    1.380940
SBUX    1.293998
          ...   
VZ     -0.986293
LUV    -1.073091
MMM    -1.293282
CVS    -1.351760
DISH   -1.482757
Length: 95, dtype: float64


In [33]:
stock_prices = get_close(three_years_ago, yesterday, optionable_stocks)

stk_ret_3y = get_pctchge(stock_prices)
stk_ret_3y_m = get_mean(stk_ret_3y)
stk_ret_3y_sd = get_std(stk_ret_3y)
stk_ret_3y_sr = get_sharpe(stk_ret_3y_m, stk_ret_3y_sd)

stk_ret_3y_m = stk_ret_3y_m.sort_values(ascending=False)
stk_ret_3y_sd = stk_ret_3y_sd.sort_values(ascending=False)
stk_ret_3y_sr = stk_ret_3y_sr.sort_values(ascending=False)

print(stk_ret_3y_m)
print(stk_ret_3y_sd)
print(stk_ret_3y_sr)

[*********************100%***********************]  95 of 95 completed
MARA    1.909202
DVN     0.690401
OXY     0.668811
MRO     0.639717
PLUG    0.627783
          ...   
ZM     -0.100725
PYPL   -0.116281
INTC   -0.123285
DISH   -0.297332
BYND   -0.505882
Length: 95, dtype: float64
MARA    1.540063
PLUG    0.895519
SNAP    0.853761
MRNA    0.766118
BYND    0.749667
          ...   
KO      0.186189
VZ      0.183688
PG      0.176737
PEP     0.168463
JNJ     0.164861
Length: 95, dtype: float64
MARA    1.207225
MPC     1.128872
DVN     1.127451
FCX     1.087390
MRO     1.015524
          ...   
MMM    -0.420573
INTC   -0.486704
VZ     -0.651164
DISH   -0.679038
BYND   -0.741506
Length: 95, dtype: float64


In [34]:
stock_prices = get_close(five_years_ago, yesterday, optionable_stocks)

stk_ret_5y = get_pctchge(stock_prices)
stk_ret_5y_m = get_mean(stk_ret_5y)
stk_ret_5y_sd = get_std(stk_ret_5y)
stk_ret_5y_sr = get_sharpe(stk_ret_5y_m, stk_ret_5y_sd)

stk_ret_5y_m = stk_ret_5y_m.sort_values(ascending=False)
stk_ret_5y_sd = stk_ret_5y_sd.sort_values(ascending=False)
stk_ret_5y_sr = stk_ret_5y_sr.sort_values(ascending=False)

print(stk_ret_5y_m)
print(stk_ret_5y_sd)
print(stk_ret_5y_sr)

[*********************100%***********************]  95 of 95 completed
MARA    1.293156
TSLA    0.818439
MRNA    0.695050
PLUG    0.687860
NVDA    0.598722
          ...   
VZ     -0.033925
LUV    -0.052932
BYND   -0.064890
MMM    -0.069654
DISH   -0.245594
Length: 95, dtype: float64
MARA    1.453097
PLUG    0.854591
BYND    0.836630
SNAP    0.819134
MRNA    0.783777
          ...   
BMY     0.226088
KO      0.225050
PG      0.224087
JNJ     0.208774
VZ      0.200542
Length: 95, dtype: float64
TSLA    1.126496
NVDA    1.039236
AAPL    0.925023
MARA    0.855522
MRNA    0.823002
          ...   
WBA    -0.231284
LUV    -0.246267
VZ     -0.418491
MMM    -0.433612
DISH   -0.559019
Length: 95, dtype: float64


In [35]:
stock_prices = get_close(ten_years_ago, yesterday, optionable_stocks)

stk_ret_10y = get_pctchge(stock_prices)
stk_ret_10y_m = get_mean(stk_ret_10y)
stk_ret_10y_sd = get_std(stk_ret_10y)
stk_ret_10y_sr = get_sharpe(stk_ret_10y_m, stk_ret_10y_sd)

stk_ret_10y_m = stk_ret_10y_m.sort_values(ascending=False)
stk_ret_10y_sd = stk_ret_10y_sd.sort_values(ascending=False)
stk_ret_10y_sr = stk_ret_10y_sr.sort_values(ascending=False)

print(stk_ret_10y_m)
print(stk_ret_10y_sd)
print(stk_ret_10y_sr)

[*********************100%***********************]  95 of 95 completed
MARA    1.293156
TSLA    0.818439
MRNA    0.695050
PLUG    0.687860
NVDA    0.598722
          ...   
VZ     -0.033925
LUV    -0.052932
BYND   -0.064890
MMM    -0.069654
DISH   -0.245594
Length: 95, dtype: float64
MARA    1.453097
PLUG    0.854591
BYND    0.836630
SNAP    0.819134
MRNA    0.783777
          ...   
BMY     0.226088
KO      0.225050
PG      0.224087
JNJ     0.208774
VZ      0.200541
Length: 95, dtype: float64
TSLA    1.126496
NVDA    1.039236
AAPL    0.925023
MARA    0.855522
MRNA    0.823002
          ...   
WBA    -0.231284
LUV    -0.246267
VZ     -0.418492
MMM    -0.433612
DISH   -0.559019
Length: 95, dtype: float64


In [36]:
stock_prices = get_close(thirty_years_ago, yesterday, optionable_stocks)

stk_ret_30y = get_pctchge(stock_prices)
stk_ret_30y_m = get_mean(stk_ret_30y)
stk_ret_30y_sd = get_std(stk_ret_30y)
stk_ret_30y_sr = get_sharpe(stk_ret_30y_m, stk_ret_30y_sd)

stk_ret_30y_m = stk_ret_30y_m.sort_values(ascending=False)
stk_ret_30y_sd = stk_ret_30y_sd.sort_values(ascending=False)
stk_ret_30y_sr = stk_ret_30y_sr.sort_values(ascending=False)

print(stk_ret_30y_m)
print(stk_ret_30y_sd)
print(stk_ret_30y_sr)

[*********************100%***********************]  95 of 95 completed
MARA    1.293156
TSLA    0.818439
MRNA    0.695050
PLUG    0.687860
NVDA    0.598722
          ...   
VZ     -0.033925
LUV    -0.052932
BYND   -0.064890
MMM    -0.069654
DISH   -0.245594
Length: 95, dtype: float64
MARA    1.453097
PLUG    0.854591
BYND    0.836630
SNAP    0.819134
MRNA    0.783777
          ...   
BMY     0.226088
KO      0.225050
PG      0.224087
JNJ     0.208774
VZ      0.200542
Length: 95, dtype: float64
TSLA    1.126496
NVDA    1.039236
AAPL    0.925023
MARA    0.855522
MRNA    0.823002
          ...   
WBA    -0.231284
LUV    -0.246267
VZ     -0.418491
MMM    -0.433612
DISH   -0.559019
Length: 95, dtype: float64


In [37]:

stk_analysis_1y_df = pd.concat([stk_ret_1y_m,  stk_ret_1y_sd, stk_ret_1y_sr, stocks_by_sector], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio", "Sector"]
stk_analysis_1y_df.columns = columns
stk_analysis_1y_df

Mean   Std Dev  Sharpe Ratio                  Sector
NFLX  0.762248  0.515770      1.380940  Communication Services
MARA  0.722565  1.344453      0.500252               Financial
NVDA  0.698078  0.576494      1.124171              Technology
GE    0.623715  0.306495      1.871859             Industrials
SPOT  0.558349  0.544149      0.934210  Communication Services
...        ...       ...           ...                     ...
MMM  -0.308498  0.277200     -1.293282             Industrials
LUV  -0.323632  0.348183     -1.073091             Industrials
BYND -0.481058  0.920945     -0.576644      Consumer Defensive
SNAP -0.508210  0.972409     -0.574049  Communication Services
DISH -0.900520  0.641049     -1.482757  Communication Services

[95 rows x 4 columns]

In [38]:

stk_analysis_3y_df = pd.concat([stk_ret_3y_m,  stk_ret_3y_sd, stk_ret_3y_sr, stocks_by_sector], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio", "Sector"]
stk_analysis_3y_df.columns = columns
stk_analysis_3y_df

Mean   Std Dev  Sharpe Ratio                  Sector
MARA  1.909202  1.540063      1.207225               Financial
DVN   0.690401  0.568008      1.127451                  Energy
OXY   0.668811  0.636633      0.972006                  Energy
MRO   0.639717  0.580702      1.015524                  Energy
PLUG  0.627783  0.895519      0.645194             Industrials
...        ...       ...           ...                     ...
ZM   -0.100725  0.638449     -0.236079              Technology
PYPL -0.116281  0.453188     -0.366914               Financial
INTC -0.123285  0.356038     -0.486704              Technology
DISH -0.297332  0.511507     -0.679038  Communication Services
BYND -0.505882  0.749667     -0.741506      Consumer Defensive

[95 rows x 4 columns]

In [39]:

stk_analysis_5y_df = pd.concat([stk_ret_5y_m,  stk_ret_5y_sd, stk_ret_5y_sr, stocks_by_sector], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio", "Sector"]
stk_analysis_5y_df.columns = columns
stk_analysis_5y_df

Mean   Std Dev  Sharpe Ratio                  Sector
MARA  1.293156  1.453097      0.855522               Financial
TSLA  0.818439  0.682150      1.126496       Consumer Cyclical
MRNA  0.695050  0.783777      0.823002              Healthcare
PLUG  0.687860  0.854591      0.746391             Industrials
NVDA  0.598722  0.528005      1.039236              Technology
...        ...       ...           ...                     ...
VZ   -0.033925  0.200542     -0.418491  Communication Services
LUV  -0.052932  0.417971     -0.246267             Industrials
BYND -0.064890  0.836630     -0.137324      Consumer Defensive
MMM  -0.069654  0.275948     -0.433612             Industrials
DISH -0.245594  0.528773     -0.559019  Communication Services

[95 rows x 4 columns]

In [40]:

stk_analysis_10y_df = pd.concat([stk_ret_10y_m,  stk_ret_10y_sd, stk_ret_10y_sr, stocks_by_sector], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio", "Sector"]
stk_analysis_10y_df.columns = columns
stk_analysis_10y_df

Mean   Std Dev  Sharpe Ratio                  Sector
MARA  1.293156  1.453097      0.855522               Financial
TSLA  0.818439  0.682150      1.126496       Consumer Cyclical
MRNA  0.695050  0.783777      0.823002              Healthcare
PLUG  0.687860  0.854591      0.746391             Industrials
NVDA  0.598722  0.528005      1.039236              Technology
...        ...       ...           ...                     ...
VZ   -0.033925  0.200541     -0.418492  Communication Services
LUV  -0.052932  0.417971     -0.246267             Industrials
BYND -0.064890  0.836630     -0.137324      Consumer Defensive
MMM  -0.069654  0.275948     -0.433612             Industrials
DISH -0.245594  0.528773     -0.559019  Communication Services

[95 rows x 4 columns]

In [41]:

stk_analysis_30y_df = pd.concat([stk_ret_30y_m,  stk_ret_30y_sd, stk_ret_30y_sr, stocks_by_sector], axis="columns", join="inner")
columns = ["Mean", "Std Dev", "Sharpe Ratio", "Sector"]
stk_analysis_30y_df.columns = columns
stk_analysis_30y_df

Mean   Std Dev  Sharpe Ratio                  Sector
MARA  1.293156  1.453097      0.855522               Financial
TSLA  0.818439  0.682150      1.126496       Consumer Cyclical
MRNA  0.695050  0.783777      0.823002              Healthcare
PLUG  0.687860  0.854591      0.746391             Industrials
NVDA  0.598722  0.528005      1.039236              Technology
...        ...       ...           ...                     ...
VZ   -0.033925  0.200542     -0.418491  Communication Services
LUV  -0.052932  0.417971     -0.246267             Industrials
BYND -0.064890  0.836630     -0.137324      Consumer Defensive
MMM  -0.069654  0.275948     -0.433612             Industrials
DISH -0.245594  0.528773     -0.559019  Communication Services

[95 rows x 4 columns]

In [42]:
stk_analysis_1y_df.hvplot.scatter(x='Std Dev', y='Mean', by='Sector', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 1-Year View of Optionable Stock Universe')


:NdOverlay   [Sector]
   :Scatter   [Std Dev]   (Mean)

In [43]:
stk_analysis_3y_df.hvplot.scatter(x='Std Dev', y='Mean', by='Sector', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 3-Year View of Optionable Stock Universe')

:NdOverlay   [Sector]
   :Scatter   [Std Dev]   (Mean)

In [44]:
stk_analysis_5y_df.hvplot.scatter(x='Std Dev', y='Mean', by='Sector', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 5-Year View of Optionable Stock Universe')

:NdOverlay   [Sector]
   :Scatter   [Std Dev]   (Mean)

In [45]:
stk_analysis_10y_df.hvplot.scatter(x='Std Dev', y='Mean', by='Sector', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 10-Year View of Optionable Stock Universe')

:NdOverlay   [Sector]
   :Scatter   [Std Dev]   (Mean)

In [46]:
stk_analysis_30y_df.hvplot.scatter(x='Std Dev', y='Mean', by='Sector', hover_color='Ticker',
                  legend='right', height=500, width=1000, title='Mean and Standard Deviation 30-Year View of Optionable Stock Universe')

:NdOverlay   [Sector]
   :Scatter   [Std Dev]   (Mean)

## Correlation Analysis

In [47]:
sectors.hvplot().opts(height = 400,
                     width = 1000)

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [18]:
sectors_corr_30 = sectors.corr()
sectors_corr_10 = sectors_10.corr()
sectors_corr_5 = sectors_5.corr()
sectors_corr_3 = sectors_3.corr()
sectors_corr_1 = sectors_1.corr()
sectors_corr_6_months = sectors_6_months.corr()

AttributeError: 'str' object has no attribute 'corr'

In [ ]:
sns.heatmap(sectors_corr_30, cmap = 'coolwarm')

In [ ]:
sns.heatmap(sectors_corr_10, cmap = 'coolwarm')

In [ ]:
sns.heatmap(sectors_corr_5, cmap = 'coolwarm')

In [ ]:
sns.heatmap(sectors_corr_3, cmap = 'coolwarm')

In [ ]:
sns.heatmap(sectors_corr_1, cmap = 'coolwarm')

In [ ]:
sns.heatmap(sectors_corr_6_months, cmap = 'coolwarm')

## Sharpe Ratio Analysis

In [ ]:

stk_analysis_1y_shr = stk_analysis_1y_df['Sharpe Ratio'].sort_values(ascending=False)
stk_analysis_1y_shr_h = stk_analysis_1y_shr.head(20)
stk_analysis_1y_shr_t = stk_analysis_1y_shr.tail(20)

stk_analysis_1y_c1 = stk_analysis_1y_shr_h.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Top 20 Sharpe Ratio Optionable Stocks Ranking - 1 Year Window')


stk_analysis_1y_c1 

In [ ]:

stk_analysis_1y_c2 = stk_analysis_1y_shr_t.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Bottom 20 Sharpe Ratio Optionable Stocks Ranking - 1 Year Window')

stk_analysis_1y_c2

In [ ]:
stk_analysis_3y_shr = stk_analysis_3y_df['Sharpe Ratio'].sort_values(ascending=False)
stk_analysis_3y_shr_h = stk_analysis_3y_shr.head(20)
stk_analysis_3y_shr_t = stk_analysis_3y_shr.tail(20)

stk_analysis_3y_c1 = stk_analysis_3y_shr_h.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Top 20 Sharpe Ratio Optionable Stocks Ranking - 3 Year Window')


stk_analysis_3y_c1 

In [ ]:

stk_analysis_3y_c2 = stk_analysis_3y_shr_t.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Bottom 20 Sharpe Ratio Optionable Stocks Ranking - 3 Year Window')

stk_analysis_3y_c2

In [ ]:

stk_analysis_5y_shr = stk_analysis_5y_df['Sharpe Ratio'].sort_values(ascending=False)
stk_analysis_5y_shr_h = stk_analysis_5y_shr.head(20)
stk_analysis_5y_shr_t = stk_analysis_5y_shr.tail(20)

stk_analysis_5y_c1 = stk_analysis_5y_shr_h.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Top 20 Sharpe Ratio Optionable Stocks Ranking - 5 Year Window')


stk_analysis_5y_c1 

In [ ]:

stk_analysis_5y_c2 = stk_analysis_5y_shr_t.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Bottom 20 Sharpe Ratio Optionable Stocks Ranking - 5 Year Window')

stk_analysis_5y_c2

In [ ]:

stk_analysis_10y_shr = stk_analysis_10y_df['Sharpe Ratio'].sort_values(ascending=False)
stk_analysis_10y_shr_h = stk_analysis_10y_shr.head(20)
stk_analysis_10y_shr_t = stk_analysis_10y_shr.tail(20)

stk_analysis_10y_c1 = stk_analysis_10y_shr_h.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Top 20 Sharpe Ratio Optionable Stocks Ranking - 10 Year Window')


stk_analysis_10y_c1 

In [ ]:

stk_analysis_10y_c2 = stk_analysis_10y_shr_t.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Bottom 20 Sharpe Ratio Optionable Stocks Ranking - 10 Year Window')

stk_analysis_10y_c2

In [ ]:

stk_analysis_30y_shr = stk_analysis_30y_df['Sharpe Ratio'].sort_values(ascending=False)
stk_analysis_30y_shr_h = stk_analysis_30y_shr.head(20)
stk_analysis_30y_shr_t = stk_analysis_30y_shr.tail(20)

stk_analysis_30y_c1 = stk_analysis_30y_shr_h.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Top 20 Sharpe Ratio Optionable Stocks Ranking - 30 Year Window')


stk_analysis_30y_c1 

In [ ]:

stk_analysis_30y_c2 = stk_analysis_30y_shr_t.hvplot.bar(xlabel='Stock', ylabel='Sharpe Ratio', ylim=(-3, 3), height=500, width=1000).opts(
    yformatter='%.0f', title='Bottom 20 Sharpe Ratio Optionable Stocks Ranking - 30 Year Window')

stk_analysis_30y_c2

## Market Statistics Analysis Summary

### Key Learnings

# Stock Earnings and Fundamental Report

## Growth Stocks vs. Value Stocks Analysis

### Key Metrics Differentiating Groups

In [ ]:
# separate the list of stocks by sectors ==
# plot them by sectors ==
# separate them by dividend yield and p/e ratio
# Get returns for 1,3,5,10,30 years 
# calculate sharpe ratios for basckets of growth vs value
# Find the optimal balance of growth and value for each time period

In [ ]:
stocks_grouped = stocks_by_sector.groupby('Sector').count()
stocks_grouped.hvplot.bar(rot = 35,
                         width = 1000,
                         height = 400,
                         hover_color = 'orange')

In [ ]:
# "DividendYield": "0",
#   "EPS": "3.397",

for stock in stocks_by_sector['Ticker']:
    url = f'https://www.alphavantage.co/query?function=OVERVIEW&symbol={stock}&last=20&apikey={alpha_api}'
    data = requests.get(url)
    div_yield = data.json()['DividendYield']
    pe_ratio = data.json()['PERatio']
    stocks_by_sector['Dividend Yield'] = 
    


In [ ]:
url = f'https://www.alphavantage.co/query?function=OVERVIEW&symbol=tsla&last=20&apikey={alpha_api}'
data = requests.get(url)
div_yield = data.json()['DividendYield']
pe_ratio = data.json()['PERatio']

## Risk, Return Performance Differences by Growth vs. Value

## Sharpe Ratio Differences by Growth vs. Value

## Earnings Returns Hypothesis Analysis

## Null Hypothesis:
There is no difference in Risk/Returns/Sharpe Ratio within the quarterly earnings window (+/- 10 trading days) vs outside the earnings window (168 days)
## Alternative Hypothesis:
There is a difference between key statistical metrics within the +/- 10-day quarterly earnings window vs. outside the earnings window

## Stock Earnings and Fundamentals Summary

# Optimal Portfolio Analysis

Sharpe Optimized Portfolios vs. Value Optimized vs. Growth Optimized Portfolios

In [ ]:
# Create Portfolios

# value_port =

# growth_port = 

top_5_1yr = stk_analysis_1y_df.loc[['GE','CAH','MRK','NFLX','SBUX']]
top_10_1yr = stk_analysis_1y_df.loc[['GE','CAH','MRK','NFLX','SBUX','DHI','NVDA','ORCL','BA','SPOT']]

top_5_10yr = stk_analysis_10y_df.loc[['TSLA','NVDA','AAPL','MARA','MRNA']]
top_10_10yr = stk_analysis_10y_df.loc[['TSLA','NVDA','AAPL','MARA','MRNA','PLUG','MSFT','FCX','ABBV','AMD']]

top_5_30yr = stk_analysis_30y_df.loc[['TSLA','NVDA','AAPL','MARA','MRNA']]
top_10_30yr = stk_analysis_30y_df.loc[['TSLA','NVDA','AAPL','MARA','MRNA','PLUG','MSFT','FCX','ABBV','AMD']]



## Sharpe Ratio Maximization with Portfolio Adjustments Based on Basic Trading Rule

In [ ]:
spy_daily = get_close(thirty_years_ago, yesterday)
spy_200ema = spy_daily.ewm(halflife=100).mean()

In [ ]:
spy_daily.hvplot() * spy_200ema.hvplot(label = '100')

In [ ]:
bear_mask = spy_daily < spy_200ema
bull_mask = spy_daily > spy_200ema
bear = spy_daily[bear_mask].hvplot.scatter()
bull = spy_daily[bull_mask].hvplot.scatter()

bear * bull

# 

In [ ]:
comp_er_window('ibm', thirty_years_ago, yesterday, alpha_api).hvplot.bar()

In [ ]:
# convert the series to a datetime format
dates = pd.to_datetime(tsla_dates)

# create an empty list to hold the new date ranges
date_ranges = []

# loop over each date in the series
for date in dates:
    # create a date range for 10 days before and after the current date
    date_range = pd.date_range(date - pd.Timedelta(days=10), date + pd.Timedelta(days=10))
    # convert the date range to a Series object
    date_range_series = pd.Series(date_range)
    # add the date range to the list of date ranges
    date_ranges.append(date_range_series)

# concatenate the list of date ranges into a single Series object
new_dates = pd.concat(date_ranges)

# remove any duplicates and sort the new series
new_dates = pd.Series(sorted(set(new_dates)))

# print the new series
print(new_dates)

## Optimal Portfolio Analysis Summary